# MetaXcan

## Environment Setup
Please ensure the **MetaXcan repo** and **"imlabtools" env** are installed through the **terminal** before starting.<br>
Or open your terminal and install using the following commands:<br>
<h3>Clone the MetaXcan repo</h3>
<pre><code>git clone https://github.com/hakyimlab/MetaXcan
</code></pre>

<h3>Change directory</h3>
<pre><code>cd MetaXcan/software
</code></pre>

<h3>Install imlabtools Conda Environment, Load and Install to ipykernal</h3>
<pre><code>conda activate base
conda env create -f conda_env.yaml
conda activate imlabtools
python -m ipykernel install --user --name imlabtools --display-name "Python (imlabtools)"
</code></pre>

In [7]:
import os
os.system('pip3 install requests')
os.system('pip3 install futures')

0

In [4]:
# Query Data
import os
import requests
import gzip
import shutil
import tarfile
from concurrent.futures import ThreadPoolExecutor

# Initialize a session for HTTP requests
session = requests.Session()

# Download and preprocess GWAS data
def download_and_process(url, download_dir):
    filename = os.path.basename(url)
    filepath = os.path.join(download_dir, filename)
    temp_file = filepath.rstrip('.gz')
    
    # Stream download file if it does not exist
    if not os.path.exists(filepath):
        print(f"Downloading {filename}...")
        with session.get(url, stream=True) as r:
            r.raise_for_status()
            with open(filepath, 'wb') as f:
                for chunk in r.iter_content(chunk_size=8192):
                    f.write(chunk)
        print(f"Downloaded {filename} successfully.")
    
    # Process the file
    print(f"Processing {filename}...")
    with gzip.open(filepath, 'rt') as f_in, open(temp_file, 'w') as f_out:
        first_line = True
        for line in f_in:
            if first_line:
                f_out.write(line)
                first_line = False
            else:
                parts = line.split('\t')
                snp_info = parts[4].split(':')
                parts[4] = f"chr{snp_info[0]}_{snp_info[1]}_{snp_info[2]}_{snp_info[3]}_b38"
                f_out.write('\t'.join(parts))
                
    # Compress the processed file back
    with open(temp_file, 'rb') as f_in, gzip.open(filepath, 'wb') as f_out:
        shutil.copyfileobj(f_in, f_out)
    os.remove(temp_file)
    print(f"Completed processing for {filename}.")

# Download tissue models
def download_models(url, download_dir):
    filename = os.path.basename(url)
    filepath = os.path.join(download_dir, filename)
    
    # Stream download file if it does not exist
    if not os.path.exists(filepath):
        print(f"Downloading {filename}...")
        with session.get(url, stream=True) as r:
            r.raise_for_status()
            with open(filepath, 'wb') as f:
                for chunk in r.iter_content(chunk_size=8192):
                    f.write(chunk)
        print(f"Downloaded {filename} successfully.")
    
    # Extract if it's a tar file
    if filepath.endswith('.tar'):
        print(f"Extracting {filename}...")
        with tarfile.open(filepath) as tar:
            tar.extractall(path=download_dir)
        print(f"Completed extracting {filename}.")


# Define directories and URLs
base_dir = 'MetaXcan/software'
data_dir = os.path.join(base_dir, "data_covid")
model_dir = os.path.join(base_dir, "predi_models")
os.makedirs(data_dir, exist_ok=True)
os.makedirs(model_dir, exist_ok=True)

data_urls = [
"https://storage.googleapis.com/covid19-hg-public/20200915/results/20201020/COVID19_HGI_A1_ALL_20201020.txt.gz",
"https://storage.googleapis.com/covid19-hg-public/20200915/results/20201020/COVID19_HGI_A2_ALL_leave_23andme_20201020.txt.gz",
"https://storage.googleapis.com/covid19-hg-public/20200915/results/20201020/COVID19_HGI_B1_ALL_20201020.txt.gz",
"https://storage.googleapis.com/covid19-hg-public/20200915/results/20201020/COVID19_HGI_B2_ALL_leave_23andme_20201020.txt.gz",
"https://storage.googleapis.com/covid19-hg-public/20200915/results/20201020/COVID19_HGI_C1_ALL_leave_23andme_20201020.txt.gz",
"https://storage.googleapis.com/covid19-hg-public/20200915/results/20201020/COVID19_HGI_C2_ALL_leave_23andme_20201020.txt.gz",
"https://storage.googleapis.com/covid19-hg-public/20200915/results/20201020/COVID19_HGI_D1_ALL_20201020.txt.gz"
]

model_urls = [
"https://zenodo.org/record/3518299/files/mashr_eqtl.tar",
"https://zenodo.org/record/3518299/files/gtex_v8_expression_mashr_snp_smultixcan_covariance.txt.gz"
]

# Parallel processing with four worker nodes in max(Please check your PC/MAC infrastructure)
with ThreadPoolExecutor(max_workers=4) as executor:
    executor.map(lambda x: download_and_process(*x), [(url, data_dir) for url in data_urls])

with ThreadPoolExecutor(max_workers=4) as executor:
    executor.map(lambda x: download_models(*x), [(url, model_dir) for url in model_urls])


Downloaded COVID19_HGI_A2_ALL_leave_23andme_20201020.txt.gz successfully.
Processing COVID19_HGI_A2_ALL_leave_23andme_20201020.txt.gz...
Downloaded COVID19_HGI_A1_ALL_20201020.txt.gz successfully.
Processing COVID19_HGI_A1_ALL_20201020.txt.gz...
Downloaded COVID19_HGI_B2_ALL_leave_23andme_20201020.txt.gz successfully.
Processing COVID19_HGI_B2_ALL_leave_23andme_20201020.txt.gz...
Downloaded COVID19_HGI_B1_ALL_20201020.txt.gz successfully.
Processing COVID19_HGI_B1_ALL_20201020.txt.gz...
Completed processing for COVID19_HGI_A1_ALL_20201020.txt.gz.
Downloaded COVID19_HGI_C1_ALL_leave_23andme_20201020.txt.gz successfully.
Processing COVID19_HGI_C1_ALL_leave_23andme_20201020.txt.gz...
Completed processing for COVID19_HGI_B2_ALL_leave_23andme_20201020.txt.gz.
Downloaded COVID19_HGI_C2_ALL_leave_23andme_20201020.txt.gz successfully.
Processing COVID19_HGI_C2_ALL_leave_23andme_20201020.txt.gz...
Completed processing for COVID19_HGI_A2_ALL_leave_23andme_20201020.txt.gz.
Downloaded COVID19_HGI

In [1]:
# Calling runSPrediXcan.sh
!bash scripts/runSPrediXcan.sh

mkdir: Result: File exists
Running SPrediXcan for Lung with COVID19_HGI_A1_ALL_20201020.txt.gz...
INFO - Processing GWAS command line parameters
INFO - Building beta for MetaXcan/software/data_covid/COVID19_HGI_A1_ALL_20201020.txt.gz and MetaXcan/software/predi_models/eqtl/mashr/mashr_Lung.db
INFO - Reading input gwas with special handling: MetaXcan/software/data_covid/COVID19_HGI_A1_ALL_20201020.txt.gz
INFO - Processing input gwas
INFO - Aligning GWAS to models
INFO - Trimming output
INFO - Successfully parsed input gwas in 17.609579829999998 seconds
INFO - Started metaxcan process
INFO - Loading model from: MetaXcan/software/predi_models/eqtl/mashr/mashr_Lung.db
INFO - Loading covariance data from: MetaXcan/software/predi_models/eqtl/mashr/mashr_Lung.txt.gz
INFO - Processing loaded gwas
INFO - Started metaxcan association
INFO - 10 % of model's snps found so far in the gwas study
INFO - 20 % of model's snps found so far in the gwas study
INFO - 30 % of model's snps found so far in th

INFO - Processing input gwas
INFO - Aligning GWAS to models
INFO - Trimming output
INFO - Successfully parsed input gwas in 28.247006281 seconds
INFO - Started metaxcan process
INFO - Loading model from: MetaXcan/software/predi_models/eqtl/mashr/mashr_Whole_Blood.db
INFO - Loading covariance data from: MetaXcan/software/predi_models/eqtl/mashr/mashr_Whole_Blood.txt.gz
INFO - Processing loaded gwas
INFO - Started metaxcan association
INFO - 10 % of model's snps found so far in the gwas study
INFO - 20 % of model's snps found so far in the gwas study
INFO - 30 % of model's snps found so far in the gwas study
INFO - 40 % of model's snps found so far in the gwas study
INFO - 50 % of model's snps found so far in the gwas study
INFO - 60 % of model's snps found so far in the gwas study
INFO - 70 % of model's snps found so far in the gwas study
INFO - 80 % of model's snps found so far in the gwas study
INFO - 90 % of model's snps found so far in the gwas study
INFO - 95 % of model's snps used

INFO - Loading covariance data from: MetaXcan/software/predi_models/eqtl/mashr/mashr_Lung.txt.gz
INFO - Processing loaded gwas
INFO - Started metaxcan association
INFO - 10 % of model's snps found so far in the gwas study
INFO - 20 % of model's snps found so far in the gwas study
INFO - 30 % of model's snps found so far in the gwas study
INFO - 40 % of model's snps found so far in the gwas study
INFO - 50 % of model's snps found so far in the gwas study
INFO - 60 % of model's snps found so far in the gwas study
INFO - 70 % of model's snps found so far in the gwas study
INFO - 80 % of model's snps found so far in the gwas study
INFO - 90 % of model's snps found so far in the gwas study
INFO - 95 % of model's snps used
INFO - Sucessfully processed metaxcan association in 6.8913332630000035 seconds
SPrediXcan processing completed for COVID19_HGI_C2_ALL_leave_23andme_20201020.txt.gz and tissue Lung.
Running SPrediXcan for Whole_Blood with COVID19_HGI_C2_ALL_leave_23andme_20201020.txt.gz...

In [2]:
# Calling runSMultiXcan.sh
!bash scripts/runSMultiXcan.sh

Running SMultiXcan for COVID19_HGI_A1_ALL_20201020...
INFO - Creating context
INFO - Creating MetaXcan results manager
Level 9 - Loading metaxcan results/spredixcan/COVID19_HGI_A1_ALL_20201020__PM__Lung.csv
Level 9 - Loading metaxcan results/spredixcan/COVID19_HGI_A1_ALL_20201020__PM__Whole_Blood.csv
Level 9 - Building data
Level 9 - Processing Lung
Level 9 - Processing Whole_Blood
INFO - Loading genes
INFO - Context for snp covariance
INFO - Assessing GWAS-Models SNP intersection
INFO - Processing GWAS command line parameters
INFO - Reading input gwas: MetaXcan/software/data_covid/COVID19_HGI_A1_ALL_20201020.txt.gz
INFO - Processing input gwas
Level 9 - Calculating zscore from pvalue
Level 9 - Acquiring sign from beta
Level 9 - loading MetaXcan/software/predi_models/eqtl/mashr/mashr_Adipose_Subcutaneous.db
Level 9 - loading MetaXcan/software/predi_models/eqtl/mashr/mashr_Adipose_Visceral_Omentum.db
Level 9 - loading MetaXcan/software/predi_models/eqtl/mashr/mashr_Adrenal_Gland.db
Leve

Level 7 - Gene 30/22535: ENSG00000165724.5
Level 7 - Gene 31/22535: ENSG00000197070.13
Level 7 - Gene 32/22535: ENSG00000148408.12
Level 7 - Gene 33/22535: ENSG00000237419.1
Level 7 - Gene 34/22535: ENSG00000261456.5
Level 7 - Gene 35/22535: ENSG00000180525.11
Level 7 - Gene 36/22535: ENSG00000107929.14
Level 7 - Gene 37/22535: ENSG00000107937.18
Level 7 - Gene 38/22535: ENSG00000067064.10
Level 7 - Gene 39/22535: ENSG00000047056.14
Level 7 - Gene 40/22535: ENSG00000185736.15
Level 7 - Gene 41/22535: ENSG00000107959.15
Level 7 - Gene 42/22535: ENSG00000067082.14
Level 7 - Gene 43/22535: ENSG00000236990.1
Level 7 - Gene 44/22535: ENSG00000233117.2
Level 7 - Gene 45/22535: ENSG00000231298.6
Level 7 - Gene 46/22535: ENSG00000165568.17
Level 7 - Gene 47/22535: ENSG00000187134.13
Level 7 - Gene 48/22535: ENSG00000151632.17
Level 7 - Gene 49/22535: ENSG00000196139.13
Level 7 - Gene 50/22535: ENSG00000198610.10
Level 7 - Gene 51/22535: ENSG00000224034.1
Level 7 - Gene 52/22535: ENSG0000017846

Level 7 - Gene 215/22535: ENSG00000107984.9
Level 7 - Gene 216/22535: ENSG00000122952.16
Level 7 - Gene 217/22535: ENSG00000151151.5
Level 7 - Gene 218/22535: ENSG00000122873.11
Level 7 - Gene 219/22535: ENSG00000072401.14
Level 7 - Gene 220/22535: ENSG00000108064.10
Level 7 - Gene 221/22535: ENSG00000122870.11
Level 7 - Gene 222/22535: ENSG00000237949.1
Level 7 - Gene 223/22535: ENSG00000165449.11
Level 7 - Gene 224/22535: ENSG00000108091.10
Level 7 - Gene 225/22535: ENSG00000151150.21
Level 7 - Gene 226/22535: ENSG00000072422.16
Level 7 - Gene 227/22535: ENSG00000196932.11
Level 7 - Gene 228/22535: ENSG00000183346.6
Level 7 - Gene 229/22535: ENSG00000181915.4
Level 7 - Gene 230/22535: ENSG00000122877.15
Level 7 - Gene 231/22535: ENSG00000148572.15
Level 7 - Gene 232/22535: ENSG00000165476.13
Level 7 - Gene 233/22535: ENSG00000228065.10
Level 7 - Gene 234/22535: ENSG00000272892.1
Level 7 - Gene 235/22535: ENSG00000096717.11
Level 7 - Gene 236/22535: ENSG00000148634.15
Level 7 - Gene 2

Level 7 - Gene 403/22535: ENSG00000107443.15
Level 7 - Gene 404/22535: ENSG00000177853.14
Level 7 - Gene 405/22535: ENSG00000095585.16
Level 7 - Gene 406/22535: ENSG00000095587.8
Level 7 - Gene 407/22535: ENSG00000077147.14
Level 7 - Gene 408/22535: ENSG00000155629.14
Level 7 - Gene 409/22535: ENSG00000196233.12
Level 7 - Gene 410/22535: ENSG00000187122.16
Level 7 - Gene 411/22535: ENSG00000213390.10
Level 7 - Gene 412/22535: ENSG00000165879.8
Level 7 - Gene 413/22535: ENSG00000181274.6
Level 7 - Gene 414/22535: ENSG00000171314.8
Level 7 - Gene 415/22535: ENSG00000171311.12
Level 7 - Gene 416/22535: ENSG00000171307.18
Level 7 - Gene 417/22535: ENSG00000155229.20
Level 7 - Gene 418/22535: ENSG00000165886.4
Level 7 - Gene 419/22535: ENSG00000241935.8
Level 7 - Gene 420/22535: ENSG00000171160.17
Level 7 - Gene 421/22535: ENSG00000155252.13
Level 7 - Gene 422/22535: ENSG00000119986.6
Level 7 - Gene 423/22535: ENSG00000155254.12
Level 7 - Gene 424/22535: ENSG00000155256.17
Level 7 - Gene 42

Level 7 - Gene 593/22535: ENSG00000188385.11
Level 7 - Gene 594/22535: ENSG00000151640.12
Level 7 - Gene 595/22535: ENSG00000165752.16
Level 7 - Gene 596/22535: ENSG00000148814.17
Level 7 - Gene 597/22535: ENSG00000171813.13
Level 7 - Gene 598/22535: ENSG00000180066.9
Level 7 - Gene 599/22535: ENSG00000226900.1
Level 7 - Gene 600/22535: ENSG00000068383.18
Level 7 - Gene 601/22535: ENSG00000171798.17
Level 7 - Gene 602/22535: ENSG00000151650.7
Level 7 - Gene 603/22535: ENSG00000151651.15
Level 7 - Gene 604/22535: ENSG00000130640.13
Level 7 - Gene 605/22535: ENSG00000130643.8
Level 7 - Gene 606/22535: ENSG00000165828.14
Level 7 - Gene 607/22535: ENSG00000148803.11
Level 7 - Gene 608/22535: ENSG00000127884.4
Level 7 - Gene 609/22535: ENSG00000148832.15
Level 7 - Gene 610/22535: ENSG00000148824.18
Level 7 - Gene 611/22535: ENSG00000203772.7
Level 7 - Gene 612/22535: ENSG00000214279.13
Level 7 - Gene 613/22535: ENSG00000130649.9
Level 7 - Gene 614/22535: ENSG00000171772.15
Level 7 - Gene 61

...

Level 7 - Gene 21500/22535: ENSG00000248223.1
Level 7 - Gene 21501/22535: ENSG00000250822.1
Level 7 - Gene 21502/22535: ENSG00000249854.1
Level 7 - Gene 21503/22535: ENSG00000251629.6
Level 7 - Gene 21504/22535: ENSG00000249490.1
Level 7 - Gene 21505/22535: ENSG00000249359.2
Level 7 - Gene 21506/22535: ENSG00000250694.1
Level 7 - Gene 21507/22535: ENSG00000248908.1
Level 7 - Gene 21508/22535: ENSG00000251273.1
Level 7 - Gene 21509/22535: ENSG00000245662.2
Level 7 - Gene 21510/22535: ENSG00000248490.1
Level 7 - Gene 21511/22535: ENSG00000249785.1
Level 7 - Gene 21512/22535: ENSG00000259786.6
Level 7 - Gene 21513/22535: ENSG00000248391.5
Level 7 - Gene 21514/22535: ENSG00000251281.1
Level 7 - Gene 21515/22535: ENSG00000248539.1
Level 7 - Gene 21516/22535: ENSG00000249405.1
Level 7 - Gene 21517/22535: ENSG00000248789.5
Level 7 - Gene 21518/22535: ENSG00000249697.1
Level 7 - Gene 21519/22535: ENSG00000249584.1
Level 7 - Gene 21520/22535: ENSG00000251391.4
Level 7 - Gene 21521/22535: ENSG00

Level 7 - Gene 21679/22535: ENSG00000255289.1
Level 7 - Gene 21680/22535: ENSG00000251127.2
Level 7 - Gene 21681/22535: ENSG00000254119.5
Level 7 - Gene 21682/22535: ENSG00000253834.1
Level 7 - Gene 21683/22535: ENSG00000253287.1
Level 7 - Gene 21684/22535: ENSG00000253235.1
Level 7 - Gene 21685/22535: ENSG00000253238.1
Level 7 - Gene 21686/22535: ENSG00000254123.1
Level 7 - Gene 21687/22535: ENSG00000253898.1
Level 7 - Gene 21688/22535: ENSG00000253682.1
Level 7 - Gene 21689/22535: ENSG00000253749.1
Level 7 - Gene 21690/22535: ENSG00000253371.1
Level 7 - Gene 21691/22535: ENSG00000279847.3
Level 7 - Gene 21692/22535: ENSG00000253960.1
Level 7 - Gene 21693/22535: ENSG00000248762.2
Level 7 - Gene 21694/22535: ENSG00000253489.1
Level 7 - Gene 21695/22535: ENSG00000254209.1
Level 7 - Gene 21696/22535: ENSG00000254000.1
Level 7 - Gene 21697/22535: ENSG00000253470.1
Level 7 - Gene 21698/22535: ENSG00000253220.1
Level 7 - Gene 21699/22535: ENSG00000253573.1
Level 7 - Gene 21700/22535: ENSG00

Level 7 - Gene 21858/22535: ENSG00000257454.1
Level 7 - Gene 21859/22535: ENSG00000257682.1
Level 7 - Gene 21860/22535: ENSG00000257750.1
Level 7 - Gene 21861/22535: ENSG00000258332.1
Level 7 - Gene 21862/22535: ENSG00000257183.1
Level 7 - Gene 21863/22535: ENSG00000257835.1
Level 7 - Gene 21864/22535: ENSG00000258048.1
Level 7 - Gene 21865/22535: ENSG00000257747.1
Level 7 - Gene 21866/22535: ENSG00000257729.1
Level 7 - Gene 21867/22535: ENSG00000258216.5
Level 7 - Gene 21868/22535: ENSG00000257725.1
Level 7 - Gene 21869/22535: ENSG00000257787.1
Level 7 - Gene 21870/22535: ENSG00000197651.4
Level 7 - Gene 21871/22535: ENSG00000258272.1
Level 7 - Gene 21872/22535: ENSG00000257860.5
Level 7 - Gene 21873/22535: ENSG00000257762.5
Level 7 - Gene 21874/22535: ENSG00000257193.1
Level 7 - Gene 21875/22535: ENSG00000256560.1
Level 7 - Gene 21876/22535: ENSG00000257603.1
Level 7 - Gene 21877/22535: ENSG00000257997.5
Level 7 - Gene 21878/22535: ENSG00000257476.1
Level 7 - Gene 21879/22535: ENSG00

Level 7 - Gene 22049/22535: ENSG00000261029.1
Level 7 - Gene 22050/22535: ENSG00000261176.1
Level 7 - Gene 22051/22535: ENSG00000261177.1
Level 7 - Gene 22052/22535: ENSG00000269826.1
Level 7 - Gene 22053/22535: ENSG00000260507.1
Level 7 - Gene 22054/22535: ENSG00000181323.7
Level 7 - Gene 22055/22535: ENSG00000266279.1
Level 7 - Gene 22056/22535: ENSG00000273816.1
Level 7 - Gene 22057/22535: ENSG00000273098.1
Level 7 - Gene 22058/22535: ENSG00000234634.1
Level 7 - Gene 22059/22535: ENSG00000233852.1
Level 7 - Gene 22060/22535: ENSG00000265163.1
Level 7 - Gene 22061/22535: ENSG00000233193.1
Level 7 - Gene 22062/22535: ENSG00000237057.2
Level 7 - Gene 22063/22535: ENSG00000264765.1
Level 7 - Gene 22064/22535: ENSG00000267075.1
Level 7 - Gene 22065/22535: ENSG00000264422.1
Level 7 - Gene 22066/22535: ENSG00000178130.9
Level 7 - Gene 22067/22535: ENSG00000261020.1
Level 7 - Gene 22068/22535: ENSG00000264262.1
Level 7 - Gene 22069/22535: ENSG00000263567.1
Level 7 - Gene 22070/22535: ENSG00

Level 7 - Gene 22230/22535: ENSG00000225588.2
Level 7 - Gene 22231/22535: ENSG00000239498.1
Level 7 - Gene 22232/22535: ENSG00000283408.1
Level 7 - Gene 22233/22535: ENSG00000267732.1
Level 7 - Gene 22234/22535: ENSG00000158901.11
Level 7 - Gene 22235/22535: ENSG00000256637.6
Level 7 - Gene 22236/22535: ENSG00000229457.1
Level 7 - Gene 22237/22535: ENSG00000228650.2
Level 7 - Gene 22238/22535: ENSG00000213121.2
Level 7 - Gene 22239/22535: ENSG00000221933.2
Level 7 - Gene 22240/22535: ENSG00000221938.4
Level 7 - Gene 22241/22535: ENSG00000212807.1
Level 7 - Gene 22242/22535: ENSG00000236130.1
Level 7 - Gene 22243/22535: ENSG00000258853.1
Level 7 - Gene 22244/22535: ENSG00000268186.1
Level 7 - Gene 22245/22535: ENSG00000237396.1
Level 7 - Gene 22246/22535: ENSG00000010256.10
Level 7 - Gene 22247/22535: ENSG00000186451.1
Level 7 - Gene 22248/22535: ENSG00000283383.1
Level 7 - Gene 22249/22535: ENSG00000231877.1
Level 7 - Gene 22250/22535: ENSG00000237921.2
Level 7 - Gene 22251/22535: ENSG

In [5]:
# Remove MetaXcan (If you don't need anymore)
!rm -rf MetaXcan

rm: MetaXcan: No such file or directory


# POPS

# Environment Setup
Please clone the pops repo through the terminal and download the **pops pipeline data**, **magma software** and **gene features** inside the pops data folder before starting, and arrange the feature folders according to the Tips below<br>

<h3>Download pops github repo</h3>
<pre><code>git clone https://github.com/FinucaneLab/pops.git
</code></pre>

<h3> Change directory to pops</h3>
<pre><code>cd pops/
</code></pre>

<h3>Download PoPS Pipeline Data</h3>
<pre><code>Please choose the gene prioritization results to download and save as data in pops.
<a href="https://www.finucanelab.org/data">Finucane Lab Data</a>
</code></pre>

<h3>Download Magma software</h3>
<pre><code>Please find the compiler and operation system that suits you, and unzip to the pops folder!
<a href="https://cncr.nl/research/magma/">CNCR CTG Lab Magma</a>
</code></pre>

<h3>Download Gene Features</h3>
<pre><code>We use human_lung and human_pbmc for COVID19 pops pipeline 
<a href="https://github.com/FinucaneLab/gene_features/tree/master/features">Finucane Lab Features</a>
</code></pre>

<div style="background-color: #ADD8E6; color: black; border-left: 5px solid black; padding: 10px;">
    <b>Tip:</b> Please refer to the pops example's data folder and arrange human_lung and human_pbmc similarly. This means you can create human_lung and humna_pmbc folders under the data folder and copy four folders (features_munged,features_raw,magma_scores, and utils) from the example data for each, replacing the files in features_raw with the download features(keep GTEx.txt). 
</div>

In [4]:
import os
import requests
import gzip
import shutil
from concurrent.futures import ThreadPoolExecutor

# Download and preprocessing COVID19 GWAS Summary data (TO DO: Merge with the MetaXcan data preparation)
download_dir = "pops/data/data_covid"
os.makedirs(download_dir, exist_ok=True)

urls = [
    "https://storage.googleapis.com/covid19-hg-public/20200915/results/20201020/COVID19_HGI_A1_ALL_20201020.txt.gz",
    "https://storage.googleapis.com/covid19-hg-public/20200915/results/20201020/COVID19_HGI_A2_ALL_leave_23andme_20201020.txt.gz",
    "https://storage.googleapis.com/covid19-hg-public/20200915/results/20201020/COVID19_HGI_B1_ALL_20201020.txt.gz",
    "https://storage.googleapis.com/covid19-hg-public/20200915/results/20201020/COVID19_HGI_B2_ALL_leave_23andme_20201020.txt.gz",
    "https://storage.googleapis.com/covid19-hg-public/20200915/results/20201020/COVID19_HGI_C1_ALL_leave_23andme_20201020.txt.gz",
    "https://storage.googleapis.com/covid19-hg-public/20200915/results/20201020/COVID19_HGI_C2_ALL_leave_23andme_20201020.txt.gz",
    "https://storage.googleapis.com/covid19-hg-public/20200915/results/20201020/COVID19_HGI_D1_ALL_20201020.txt.gz",
]

def download_and_unzip(url):
    local_filename = url.split('/')[-1]
    dest_path = os.path.join(download_dir, local_filename)
    txt_filename = local_filename.rstrip('.gz')
    txt_path = os.path.join(download_dir, txt_filename)

    if not os.path.exists(dest_path):
        print(f"Downloading {local_filename}...")
        response = requests.get(url, stream=True)
        response.raise_for_status()  # Check for errors
        with open(dest_path, 'wb') as f:
            for chunk in response.iter_content(chunk_size=8192):
                f.write(chunk)

    print(f"Unzipping {local_filename}...")
    with gzip.open(dest_path, 'rb') as f_in:
        with open(txt_path, 'wb') as f_out:
            shutil.copyfileobj(f_in, f_out)

    os.remove(dest_path)  # Remove all .gz files
    print(f"Completed {local_filename}.")

# Download and unzip files in parallel
with ThreadPoolExecutor(max_workers=4) as executor:
    executor.map(download_and_unzip, urls)

# Merge all COVID19 GWAS summary files into one
summary_stats_path = os.path.join(download_dir, "COVID19_GWAS_summary_stats.txt")

# Sort the files Before merging
txt_files = [f for f in os.listdir(download_dir) if f.endswith(".txt")]
txt_files.sort()

with open(summary_stats_path, 'wb') as outfile:
    for i, filename in enumerate(txt_files):
        file_path = os.path.join(download_dir, filename)
        with open(file_path, 'rb') as readfile:
            # Skip the header for all but the first file
            if i != 0:
                next(readfile)  # Skip the first line (header) of subsequent files
            shutil.copyfileobj(readfile, outfile)

# Remove all .txt files 
for filename in txt_files:
    if filename != os.path.basename(summary_stats_path):
        os.remove(os.path.join(download_dir, filename))

print("All files downloaded, unzipped, and combined.")


Unzipping COVID19_HGI_B1_ALL_20201020.txt.gz...
Unzipping COVID19_HGI_A2_ALL_leave_23andme_20201020.txt.gz...
Unzipping COVID19_HGI_A1_ALL_20201020.txt.gz...
Unzipping COVID19_HGI_B2_ALL_leave_23andme_20201020.txt.gz...
Completed COVID19_HGI_A1_ALL_20201020.txt.gz.
Completed COVID19_HGI_A2_ALL_leave_23andme_20201020.txt.gz.
Completed COVID19_HGI_B1_ALL_20201020.txt.gz.
Completed COVID19_HGI_B2_ALL_leave_23andme_20201020.txt.gz.
Unzipping COVID19_HGI_C1_ALL_leave_23andme_20201020.txt.gz...
Unzipping COVID19_HGI_D1_ALL_20201020.txt.gz...
Unzipping COVID19_HGI_C2_ALL_leave_23andme_20201020.txt.gz...
Completed COVID19_HGI_C1_ALL_leave_23andme_20201020.txt.gz.
Completed COVID19_HGI_D1_ALL_20201020.txt.gz.
Completed COVID19_HGI_C2_ALL_leave_23andme_20201020.txt.gz.
All files downloaded, unzipped, and combined.


## hg38 reference panel
The PoPS Pipeline Data includes a reference panel of 1000G.EUR European genome data. If you want to use hg38 instead, please download the Plink 2.0 software and move its executable file "plink2.0" to the pops folder so the following script can run.
<h3>Download Plink</h3>
Please choose the operation system and version that suits you, and unzip it to the pops folder!
<pre><code><a href="https://www.cog-genomics.org/plink/2.0/">Christopher Chang Plink</a>
</code></pre>

<div style="background-color: pink; color: black; border-left: 5px solid black; padding: 10px;">
    <b>Tip:</b> The common system path in Mac is "/usr/local/bin/" or "~/bin/" After placing the executed file, you can use plink or plink --version to check if the installation succeeded.
</div>

In [3]:
# Create hg38 reference panel
!yes | bash scripts/getRefHg38.sh

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100    62    0    62    0     0    322      0 --:--:-- --:--:-- --:--:--   321
100   320  100   320    0     0    429      0 --:--:-- --:--:-- --:--:--   429
100 3239M  100 3239M    0     0  56.0M      0  0:00:57  0:00:57 --:--:-- 61.4M 0  47.5M      0  0:01:08  0:00:16  0:00:52 55.6M
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100   240    0   240    0     0    324      0 --:--:-- --:--:-- --:--:--   324
100   475    0   475    0     0    285      0 --:--:--  0:00:01 --:--:--     0
100 2748M  100 2748M    0     0  56.3M      0  0:00:48  0:00:48 --:--:-- 67.6M  51.0M      0  0:00:53  0:00:28  0:00:25 61.9M
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 D

# Add codes to solve a common problem before piping 
The "ValueError: shapes (18383,743) and (1867) not aligned: 743 (dim 1) != 1867 (dim 0)" issue is caused by the duplicated name in the generated matrix table. A **solution provided by Vinodsri** in the GitHub issue is adding codes renaming the feature clusters in the **munge_feature_directory.py** script.

<h3>Insert the code chunk in the position and import os</h3>
<pre><code>
import os
    
for f in all_feature_files:
    f_df = pd.read_csv(f, sep="\t", index_col=0).astype(np.float64)
    f_df = gene_annot_df.merge(
        f_df, how="left", left_index=True, right_index=True)
    <span style="color: brown;"># Add the following three line codes accordingly to munge_feature_directory.py</span>
    base_filename = os.path.basename(f)
    fname = base_filename.replace(r".txt.gz", "_")
    f_df.columns = f_df.columns.str.replace(r"Cluster", fname)
    <span style="color: brown;"># -----------------------------  by vinodhsri  ------------------------------</span>
    if nan_policy == "raise":
        assert not f_df.isnull().values.any(), "Missing genes in feature matrix."
</code></pre>

<h3>Now, that's start the pops pipelines with hg38 reference panel! </h3>

In [4]:
# Calling Pops0 step 
!bash scripts/runPopsi0.sh

Process feature files to feature matrix file...
Feature matrix process completed


In [7]:
# Calling Pops1 step
!bash scripts/runPopsi1.sh

Calculate magma score for each GWAS summary statistic file...
Welcome to MAGMA v1.10 (custom)
Using flags:
	--bfile pops/data/all_hg38
	--gene-annot pops/data/magma_0kb.genes.annot
	--pval pops/data/data_covid/COVID19_GWAS_summary_stats.txt use=13,9 ncol=11
	--gene-model snp-wise=mean
	--out pops/data/human_lung/magma_scores/lung-COVID19

Start time is 13:40:53, Saturday 18 May 2024

Loading PLINK-format data...
Reading file pops/data/all_hg38.fam... 3202 individuals read
Reading file pops/data/all_hg38.bim... 70883903 SNPs read
Preparing file pops/data/all_hg38.bed... 

Reading SNP p-values from file pops/data/data_covid/COVID19_GWAS_summary_stats.txt... 
	detected 13 variables in file
	using variable: variable 13 (SNP id)
	using variable: variable 9 (p-value)
	using variable: variable 11 (sample size; discarding SNPs with N < 50)
	read 84817347 lines from file, containing valid SNP p-values for 2588143 SNPs in data (3.051% of lines, 3.454% of SNPs in data)
	         dropped all occur

In [9]:
# Calling Pops2 step
!bash scripts/runPopsi2.sh

Run Pops for COVID19 GWAS summary statistic file...
Pops COVID19 pipeline completed


In [13]:
# Remove pops (If you don't need anymore)
!rm -rf pops

# ABC

## Environment Setup
The ABC Model and COGS require CrossMap to convert the reference genome from hg19 to hg38. Please prepare your conda environment, 
or make one to install via terminal.<br>

<h3>Create Conda Env</h3>
<pre><code>
conda create -n ABCOGS python=3.9
conda activate ABCOGS
pip3 install CrossMap
pip3 install pandas
pip3 install pyranges
pip3 install biopython
conda install ipykernel
conda install -c conda-forge notebook
python -m ipykernel install --user --name ABCOGS --display-name "Python (ABCOGS)"
</code></pre>



In [2]:
# Data Preparation

## Get fine-mapping, ABC predictions, chain and fa file
!mkdir -p ABC && cd ABC && \
wget https://storage.googleapis.com/covid19-hg-in-silico-followup/V4/finemapping/COVID19_HGI_20201020_ABF.tar.gz && \
gzip -d COVID19_HGI_20201020_ABF.tar.gz && \
tar -xf COVID19_HGI_20201020_ABF.tar && \
rm COVID19_HGI_20201020_ABF.tar && \
wget https://mitra.stanford.edu/engreitz/oak/public/Nasser2021/AllPredictions.AvgHiC.ABC0.015.minus150.ForABCPaperV3.txt.gz && \
gzip -d AllPredictions.AvgHiC.ABC0.015.minus150.ForABCPaperV3.txt.gz && \
wget https://hgdownload.soe.ucsc.edu/goldenPath/hg38/bigZips/hg38.fa.gz && \
wget https://hgdownload.cse.ucsc.edu/goldenpath/hg19/liftOver/hg19ToHg38.over.chain.gz && \
gzip -d hg38.fa.gz && \
cd ..

## Ensembl hg38 annotation file
# https://useast.ensembl.org/biomart/martview/75c3078f9cf760aa9f485728508be51b
# Download the columns * Chromosome/scaffold name * Gene start (bp) * Gene end (bp) * Gene stable ID * Gene name * Strand * Gene type
# Save as hg38_ensembl.txt and hg38_ensembl.bed

--2024-05-18 15:44:33--  https://storage.googleapis.com/covid19-hg-in-silico-followup/V4/finemapping/COVID19_HGI_20201020_ABF.tar.gz
Resolving storage.googleapis.com (storage.googleapis.com)... 142.251.32.123, 142.251.40.123, 142.250.80.91, ...
Connecting to storage.googleapis.com (storage.googleapis.com)|142.251.32.123|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 41623576 (40M) [application/x-gzip]
Saving to: ‘COVID19_HGI_20201020_ABF.tar.gz’

COVID19_HGI_2020102 100%[===================>]  39.70M  37.1MB/s    in 1.1s    

2024-05-18 15:44:35 (37.1 MB/s) - ‘COVID19_HGI_20201020_ABF.tar.gz’ saved [41623576/41623576]

--2024-05-18 15:44:36--  https://mitra.stanford.edu/engreitz/oak/public/Nasser2021/AllPredictions.AvgHiC.ABC0.015.minus150.ForABCPaperV3.txt.gz
Resolving mitra.stanford.edu (mitra.stanford.edu)... 171.67.96.243
Connecting to mitra.stanford.edu (mitra.stanford.edu)|171.67.96.243|:443... connected.
HTTP request sent, awaiting response... 200 OK
L

In [3]:
# Convert ABC result from hg19 to hg38
!awk 'BEGIN {OFS="\t"; print "chr", "start", "end", "idx"} NR > 1 {print $1, $2, $3, NR-1}' ABC/AllPredictions.AvgHiC.ABC0.015.minus150.ForABCPaperV3.txt > ABC/abc_result_hg19.bed
!crossmap bed ABC/hg19ToHg38.over.chain.gz ABC/abc_result_hg19.bed ABC/abc_result_hg38.bed
!echo -e "chr\tstart\tend\tidx" > ABC/abc_result_hg38wH.bed && cat ABC/abc_result_hg38.bed >> ABC/abc_result_hg38wH.bed
!rm ABC/abc_result_hg38.bed

2024-05-18 03:52:52 [INFO]  Read the chain file "ABC/hg19ToHg38.over.chain.gz" 
Start coordinate is not an integer. skip chr	start	end	idx


In [7]:
# hg19 to hg38 Harmonization
import pandas as pd

try:
    abc38 = pd.read_csv('ABC/abc_result_hg38wH.bed',
                        sep='\t', header=0)
    abc19 = pd.read_csv('ABC/abc_result_hg19.bed',
                        sep='\t', header=0)
except FileNotFoundError as e:
    print(f"Error: File not found {e.filename}")
except Exception as e:
    print(f"An error occurred: {e}")

# Calculate counts of each idx in both datasets
abc19_counts = abc19['idx'].value_counts()
abc38_counts = abc38['idx'].value_counts()

# Convert to DataFrame for easier comparison
df_abc19_idxes = abc19_counts.reset_index()
df_abc19_idxes.columns = ['idx', 'abc19_counts']  # Corrected column name here

df_abc38_idxes = abc38_counts.reset_index()
df_abc38_idxes.columns = ['idx', 'abc38_counts']  # Already correctly set

# Merge counts on idx
merged_counts_idxes = pd.merge(
    df_abc19_idxes, df_abc38_idxes, on='idx', how='outer').fillna(0)

# Convert counts to integers after filling NA
merged_counts_idxes['abc19_counts'] = merged_counts_idxes['abc19_counts'].astype(
    int)
merged_counts_idxes['abc38_counts'] = merged_counts_idxes['abc38_counts'].astype(
    int)

# Output increased idx
increased_idxes = merged_counts_idxes[merged_counts_idxes['abc38_counts']
                                      > merged_counts_idxes['abc19_counts']]

# Handle increases 
abc38_merged = abc38.merge(increased_idxes, on='idx', how='left')
abc38_merged['row_number'] = abc38_merged.groupby('idx').cumcount()
abc38_filtered = abc38_merged[abc38_merged['row_number'] < abc38_merged['abc19_counts'].fillna(float('inf'))]
abc38 = abc38_filtered.drop(columns=['abc19_counts', 'row_number','abc38_counts'])

# Handling Missing idx
ids_abc19 = set(abc19['idx'])
ids_abc38 = set(abc38['idx'])

missing_in_abc38 = ids_abc19.difference(ids_abc38)
missing_abc19_data = abc19[abc19['idx'].isin(missing_in_abc38)]

# Create rows for missing IDs with NaN for chr, start, and end
missing_rows = [{
    'chr': row['chr'],
    'start': pd.NA,
    'end': pd.NA,
    'idx': row['idx'],
} for _, row in missing_abc19_data.iterrows()]


# Append missing rows to oe38 using pd.concat
missing_df = pd.DataFrame(missing_rows)
abc38_complete = pd.concat([abc38, missing_df], ignore_index=True)

outfile = 'ABC/final_abc38_complete.bed'
# Save the filtered hg38 dataset
abc38_complete.to_csv(outfile, sep='\t', index=False)
print(f'Harmonization successfully created and save as: {outfile}')

Harmonization successfully created and save as: ABC/final_abc38_complete.bed


In [11]:
# Update ABC Allpredictions
import pandas as pd

# Load the original data
original_df = pd.read_csv(
    'ABC/AllPredictions.AvgHiC.ABC0.015.minus150.ForABCPaperV3.txt', sep='\t')

# Load the converted coordinates data
converted_df = pd.read_csv('ABC/final_abc38_complete.bed', sep='\t')

# Ensure that the 'idx' column in the converted DataFrame is of the right data type
converted_df['idx'] = converted_df['idx'].astype(int)

# Add an 'idx' column to the original DataFrame that matches the row index + 1 (to match your 1-based idx)
original_df['idx'] = range(1, len(original_df) + 1)

# Merge the original DataFrame with the converted coordinates on 'idx'
merged_df = pd.merge(original_df, converted_df[[
                     'chr', 'start', 'end', 'idx']], on='idx', suffixes=('', '_converted'))

# Update the original 'chr', 'start', and 'end' columns with the converted values
merged_df['chr'] = merged_df['chr_converted']
merged_df['start'] = merged_df['start_converted']
merged_df['end'] = merged_df['end_converted']


# Drop the converted columns as they are no longer needed
merged_df.drop(['chr_converted', 'start_converted',
               'end_converted'], axis=1, inplace=True)

merged_df.drop(['idx'], axis=1, inplace=True)

# Save the updated DataFrame to a new file
outfile = 'ABC/ABC_AllPredictions_hg38.txt'
merged_df.to_csv(outfile, sep='\t', index=False)

print(f'ABC.Predicitons coordinats successfully updated and save as: {outfile}')

ABC.Predicitons coordinats successfully updated and save as: ABC/ABC_AllPredictions_hg38.txt


In [12]:
import pandas as pd
import pyranges as pr
import warnings

warnings.filterwarnings("ignore", category=FutureWarning)

# Prepare abc_hg38 data
abc_hg38_df = pd.read_csv('ABC/ABC_AllPredictions_hg38.txt', sep='\t')
abc_hg38_df.dropna(subset=['start', 'end'], inplace=True)
abc_hg38_df = abc_hg38_df.astype({'start': int, 'end': int})
abc_hg38_df.rename(columns={"chr": "Chromosome",
                   "start": "Start", "end": "End"}, inplace=True)
abc_hg38_df['Chromosome'] = abc_hg38_df['Chromosome'].astype(str)
abc_hg38_df.dropna(subset=['Start', 'End', 'Chromosome'], inplace=True)
abc_hg38_ranges = pr.PyRanges(abc_hg38_df)



# Prepare fine-mapping files
directory_path = 'ABC/COVID19_HGI_20201020_ABF/results/'
fine_mapping_files = [
    'COVID19_HGI_A2_ALL_leave_23andme_20201020.ABF.snp.bgz',
    'COVID19_HGI_B1_ALL_20201020.ABF.snp.bgz',
    'COVID19_HGI_B2_ALL_leave_23andme_20201020.ABF.snp.bgz',
    'COVID19_HGI_C1_ALL_leave_23andme_20201020.ABF.snp.bgz',
    'COVID19_HGI_C2_ALL_leave_23andme_20201020.ABF.snp.bgz',
    'COVID19_HGI_D1_ALL_20201020.ABF.snp.bgz',
]

# Prepare ensembl annotation file
annotation_data = pd.read_csv('ABC/hg38_ensembl.txt', sep='\t')
annotation_data['Chromosome'] = 'chr' + annotation_data['Chromosome/scaffold name'].astype(str)
annotation_data['Start'] = annotation_data['Gene start (bp)']
annotation_data['End'] = annotation_data['Gene end (bp)']
annotation_data = annotation_data[['Chromosome', 'Start', 'End', 'Gene stable ID']]


annotation_ranges = pr.PyRanges(annotation_data)


# Process each file
for file_name in fine_mapping_files:
    file_path = directory_path + file_name
    try:
        df_variants = pd.read_csv(
            file_path, compression='gzip', sep='\t', header=0)
        if 'cs_99' not in df_variants.columns or 'position' not in df_variants.columns or 'chromosome' not in df_variants.columns:
            print(f"Missing required columns in {file_name}.")
            continue
        # Filter variants by cs_99 ==1
        filtered_df = df_variants[df_variants['cs_99'] == 1]
        filtered_df = filtered_df.dropna(subset=['position'])
        filtered_df.loc[:, 'position'] = filtered_df['position'].astype(int)
        filtered_df.loc[:,
                        'Chromosome'] = filtered_df['chromosome'].astype(str)
        filtered_df.loc[:, 'Start'] = filtered_df['position']
        filtered_df.loc[:, 'End'] = filtered_df['position']
        filtered_df = filtered_df.dropna(subset=['Chromosome', 'Start', 'End'])

        gr_variants = pr.PyRanges(filtered_df[['Chromosome', 'Start', 'End']])
        
        # Map SNP position to promoter region
        overlaps = abc_hg38_ranges.join(gr_variants, suffix='_variant')
        print(overlaps)
        annotated_overlap=overlaps.join(annotation_ranges, suffix='_annotation')
        print(annotated_overlap)
        result_df = annotated_overlap.df

        # Sort results by ABC.Score in descending order
        if 'ABC.Score' in result_df.columns:
            result_df = result_df.sort_values(by='ABC.Score', ascending=False)
        
        output_filename = 'ABC_results_' + file_name.replace('.ABF.snp.bgz', '.tsv')
        result_df.to_csv(directory_path + output_filename,
                         sep='\t', index=False)
        print(f"Results saved successfully for {output_filename}")
    except Exception as e:
        print(f"An error occurred while processing {file_name}: {e}")

+--------------+-----------+-----------+-------+
| Chromosome   | Start     | End       | +23   |
| (category)   | (int64)   | (int64)   | ...   |
|--------------+-----------+-----------+-------|
| chr3         | 45817522  | 45818315  | ...   |
| chr3         | 45817559  | 45818328  | ...   |
| chr3         | 45817559  | 45818328  | ...   |
| chr3         | 45817559  | 45818328  | ...   |
| ...          | ...       | ...       | ...   |
| chr21        | 42389672  | 42389872  | ...   |
| chr21        | 42390308  | 42390999  | ...   |
| chr21        | 42390308  | 42390999  | ...   |
| chr21        | 42390308  | 42390999  | ...   |
+--------------+-----------+-----------+-------+
Unstranded PyRanges object has 25,072 rows and 26 columns from 4 chromosomes.
For printing, the PyRanges was sorted on Chromosome.
23 hidden columns: name, class, activity_base, TargetGene, ... (+ 19 more.)
+--------------+-----------+-----------+-------+
| Chromosome   | Start     | End       | +26   |
| (catego

In [19]:
directory_path = 'ABC/COVID19_HGI_20201020_ABF/results/'
output_path = 'results/ABC/' 
fine_mapping_files = [
    'ABC_results_COVID19_HGI_A2_ALL_leave_23andme_20201020.tsv',
    'ABC_results_COVID19_HGI_B1_ALL_20201020.tsv',
    'ABC_results_COVID19_HGI_B2_ALL_leave_23andme_20201020.tsv',
    'ABC_results_COVID19_HGI_C1_ALL_leave_23andme_20201020.tsv',
    'ABC_results_COVID19_HGI_C2_ALL_leave_23andme_20201020.tsv',
    'ABC_results_COVID19_HGI_D1_ALL_20201020.tsv',
]
os.makedirs(output_path, exist_ok=True)


abc_all = pd.DataFrame()

for file_name in fine_mapping_files:
    file_path = directory_path + file_name
    try:
        df_variants = pd.read_csv(file_path, sep='\t')
        if not df_variants.empty:
            abc_all = pd.concat([abc_all, df_variants], ignore_index=True)
        else:
            print(f"Data frame is empty after loading: {file_name}")
    except Exception as e:
        print(f"An error occurred while reading {file_name}: {e}")

abc_all = abc_all.drop_duplicates(subset=['Gene stable ID', 'TargetGene'])
try:
    abc_all['Chromosome'] = abc_all['Chromosome'].str.replace('chr', '').astype(int)
    abc_all.sort_values('Chromosome', inplace=True)
    abc_all['Chromosome'] = 'chr' + abc_all['Chromosome'].astype(str)
except ValueError as e:
    print('If your result includes chromosome X and Y, please change this code accordingly')

# Merged Result
abc_all_path = os.path.join(output_path, 'abc_all.tsv')

# For PPI analysis used
abc_ensg = abc_all[['Gene stable ID', 'ABC.Score']].sort_values(by='ABC.Score', ascending=False)
abc_ensg_path = os.path.join(output_path, 'abc_ensg.tsv')

abc_all.to_csv(abc_all_path, sep='\t', index=False)
abc_ensg.to_csv(abc_ensg_path, sep='\t', index=False) 
print(f'file processed and save to {abc_ensg_path} and {abc_all_path}')

# Keep the ABC result
for file_name in fine_mapping_files:
    source_path = os.path.join(directory_path, file_name)
    if os.path.exists(source_path):
        destination_path = os.path.join(output_path, file_name)
        shutil.move(source_path, destination_path)
        print(f"Moved {file_name} to {destination_path}")
    else:
        print(f"File not found: {source_path}")

An error occurred while reading ABC_results_COVID19_HGI_A2_ALL_leave_23andme_20201020.tsv: [Errno 2] No such file or directory: 'ABC/COVID19_HGI_20201020_ABF/results/ABC_results_COVID19_HGI_A2_ALL_leave_23andme_20201020.tsv'
An error occurred while reading ABC_results_COVID19_HGI_C1_ALL_leave_23andme_20201020.tsv: No columns to parse from file
file processed and save to results/ABC/abc_ensg.tsv and results/ABC/abc_all.tsv
File not found: ABC/COVID19_HGI_20201020_ABF/results/ABC_results_COVID19_HGI_A2_ALL_leave_23andme_20201020.tsv
Moved ABC_results_COVID19_HGI_B1_ALL_20201020.tsv to results/ABC/ABC_results_COVID19_HGI_B1_ALL_20201020.tsv
Moved ABC_results_COVID19_HGI_B2_ALL_leave_23andme_20201020.tsv to results/ABC/ABC_results_COVID19_HGI_B2_ALL_leave_23andme_20201020.tsv
Moved ABC_results_COVID19_HGI_C1_ALL_leave_23andme_20201020.tsv to results/ABC/ABC_results_COVID19_HGI_C1_ALL_leave_23andme_20201020.tsv
Moved ABC_results_COVID19_HGI_C2_ALL_leave_23andme_20201020.tsv to results/ABC/A

In [20]:
# Remove ABC (If you don't need anymore)
!rm -rf ABC

# COGS

## Environment Setup
If you have already installed CrossMap and other packages, please skip this installation. Otherwise, please follow the instructions in the ABC pipeline. Then, clone the rCOGS repo and install VEP <br>

<h3>COGS Repo</h3>
<pre><code>
git clone https://github.com/ollyburren/rCOGS.git
</code></pre>

<h3>ensembl-VEP installation</h3>
<pre><code>
git clone https://github.com/Ensembl/ensembl-vep.git
cd ensembl-vep
perl INSTALL.pl
cd ..
<a href="https://useast.ensembl.org/info/docs/tools/vep/script/vep_download.html">Link to ensembl-VEP Download Page</a>
</code></pre>

In [22]:
# Data Preparation

# Region file Hapmap II hg38
!wget -O rCOGS/data/genetic_map_hg38_withX.txt.gz https://storage.googleapis.com/broad-alkesgroup-public/Eagle/downloads/tables/genetic_map_hg38_withX.txt.gz

# Finemapping files
!wget -O rCOGS/data/COVID19_HGI_20201020_ABF.tar.gz https://storage.googleapis.com/covid19-hg-in-silico-followup/V4/finemapping/COVID19_HGI_20201020_ABF.tar.gz
!tar -xzf rCOGS/data/COVID19_HGI_20201020_ABF.tar.gz -C rCOGS/data/
!rm rCOGS/data/COVID19_HGI_20201020_ABF.tar.gz

# pcHi-C Peak Matrix 
!wget -O rCOGS/data/PCHiC_peak_matrix_cutoff5.txt.gz https://osf.io/download/63hh4/
!gzip -d rCOGS/data/PCHiC_peak_matrix_cutoff5.txt.gz
    
# Chain and fa file for conversion
!wget -O rCOGS/data/hg38.fa.gz https://hgdownload.soe.ucsc.edu/goldenPath/hg38/bigZips/hg38.fa.gz
!wget -O rCOGS/data/hg19ToHg38.over.chain.gz https://hgdownload.cse.ucsc.edu/goldenpath/hg19/liftOver/hg19ToHg38.over.chain.gz
!gzip -d rCOGS/data/hg38.fa.gz
!gzip -d rCOGS/data/hg19ToHg38.over.chain.gz

# Ensembl hg38 annotation file
# https://useast.ensembl.org/biomart/martview/75c3078f9cf760aa9f485728508be51b
# Download the columns * Chromosome/scaffold name * Gene start (bp) * Gene end (bp) * Gene stable ID * Gene name * Strand * Gene type
# Save as hg38_ensembl.txt and hg38_ensembl.bed to rCOGS/data/

--2024-05-18 17:39:23--  https://storage.googleapis.com/broad-alkesgroup-public/Eagle/downloads/tables/genetic_map_hg38_withX.txt.gz
Resolving storage.googleapis.com (storage.googleapis.com)... 142.250.80.59, 142.250.64.91, 172.217.165.155, ...
Connecting to storage.googleapis.com (storage.googleapis.com)|142.250.80.59|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 56334443 (54M) [text/plain]
Saving to: ‘rCOGS/data/genetic_map_hg38_withX.txt.gz’

rCOGS/data/genetic_ 100%[===================>]  53.72M  28.6MB/s    in 1.9s    

2024-05-18 17:39:25 (28.6 MB/s) - ‘rCOGS/data/genetic_map_hg38_withX.txt.gz’ saved [56334443/56334443]

--2024-05-18 17:39:26--  https://storage.googleapis.com/covid19-hg-in-silico-followup/V4/finemapping/COVID19_HGI_20201020_ABF.tar.gz
Resolving storage.googleapis.com (storage.googleapis.com)... 142.250.80.59, 142.250.64.91, 172.217.165.155, ...
Connecting to storage.googleapis.com (storage.googleapis.com)|142.250.80.59|:443... connecte

In [23]:
# Process Region file
!bash scripts/processGeneticMap2Region.sh

Process Hapmap II genetic map hg38, convert chromosome numbers, and sort directly
Compress and index the sorted BED file
Create a formatted region file with header
Region file hapmap38_recomb.bed successfully processed


In [24]:
# Process MAF and Trait Association file
!bash scripts/processMAFtraitAsso.sh

Processing COVID19_HGI_A2_ALL_leave_23andme_20201020.ABF.snp.bgz...
Processing COVID19_HGI_B1_ALL_20201020.ABF.snp.bgz...
Processing COVID19_HGI_B2_ALL_leave_23andme_20201020.ABF.snp.bgz...
Processing COVID19_HGI_C1_ALL_leave_23andme_20201020.ABF.snp.bgz...
Processing COVID19_HGI_C2_ALL_leave_23andme_20201020.ABF.snp.bgz...
Processing COVID19_HGI_D1_ALL_20201020.ABF.snp.bgz...
rCOGS/data/referenced_maf.tsv and rCOGS/data/trait_association.tsv successfully processed.


In [25]:
# Process pcHiC file
## Convert from hg19 to hg38
!sed 's/,/\t/g' rCOGS/data/PCHiC_peak_matrix_cutoff5.txt > rCOGS/data/PCHiC_peak_matrix_cutoff5.tsv
!awk '{print $1"\t"$2"\t"$3"\t"$4}' rCOGS/data/PCHiC_peak_matrix_cutoff5.tsv > rCOGS/data/bait_coordinates.bed 
!crossmap bed rCOGS/data/hg19ToHg38.over.chain rCOGS/data/bait_coordinates.bed rCOGS/data/bait_coordinates_hg38.bed
!(echo "baitChr\tbaitStart\tbaitEnd\tbaitID" && cat rCOGS/data/bait_coordinates_hg38.bed) > rCOGS/data/bait_hg38.bed

!awk '{print $6"\t"$7"\t"$8"\t"$9"\t"$4}' rCOGS/data/PCHiC_peak_matrix_cutoff5.tsv > rCOGS/data/oe_coordinates.bed
!crossmap bed rCOGS/data/hg19ToHg38.over.chain rCOGS/data/oe_coordinates.bed rCOGS/data/oe_coordinates_hg38.bed
!(echo "oeChr\toeStart\toeEnd\toeID\tbaitID" && cat rCOGS/data/oe_coordinates_hg38.bed) > rCOGS/data/oe_hg38.bed

!rm rCOGS/data/oe_coordinates_hg38.bed rCOGS/data/bait_coordinates_hg38.bed

2024-05-18 06:21:57 [INFO]  Read the chain file "rCOGS/data/hg19ToHg38.over.chain" 
Start coordinate is not an integer. skip baitChr	baitStart	baitEnd	baitID
2024-05-18 06:22:20 [INFO]  Read the chain file "rCOGS/data/hg19ToHg38.over.chain" 
Start coordinate is not an integer. skip oeChr	oeStart	oeEnd	oeID	baitID


In [26]:
## baitHarmonization
import pandas as pd

try:
    bait38 = pd.read_csv('rCOGS/data/bait_hg38.bed', sep='\t', header=0, dtype={
                         'baitID': str}, low_memory=False)
    bait37 = pd.read_csv('rCOGS/data/bait_coordinates.bed', sep='\t',
                         header=0, dtype={'baitID': str}, low_memory=False)
except FileNotFoundError as e:
    print(f"Error: File not found {e}")
except Exception as e:
    print(f"An error occurred: {e}")

# Check if two dataset have same ID
# print(set(bait37["baitID"]) == set(bait38["baitID"]))

# Calculate counts of each baitID in both datasets
count37 = bait37['baitID'].value_counts()
count38 = bait38['baitID'].value_counts()

# Convert to DataFrame for easier comparison
df_count37 = count37.reset_index()
df_count37.columns = ['baitID', 'count_hg19']

df_count38 = count38.reset_index()
df_count38.columns = ['baitID', 'count_hg38']

# Merge counts on baitID
merged_counts = pd.merge(df_count37, df_count38,
                         on='baitID', how='outer').fillna(0)

# Find baitIDs with increased counts in hg38
increased_baitIDs = merged_counts[merged_counts['count_hg38']
                                  > merged_counts['count_hg19']]

# Output increased baitIDs
print("Increased baitIDs in hg38:")
print(increased_baitIDs[['baitID', 'count_hg19', 'count_hg38']])

# Handle increases
for index, row in increased_baitIDs.iterrows():
    bait_id = row['baitID']
    count_to_keep = int(row['count_hg19'])
    rows_to_keep = bait38[bait38['baitID'] == bait_id].head(count_to_keep)

    # Filtering and keeping only the required count of duplicates
    bait38 = pd.concat([bait38[bait38['baitID'] != bait_id], rows_to_keep])

outfile = 'rCOGS/data/final_bait_coordinates_hg38.bed'
# Save the final hg38 dataset
bait38.to_csv(outfile, sep='\t', index=False)
print(f'baitHarmonization done, and save as file: {outfile}')

Increased baitIDs in hg38:
       baitID  count_hg19  count_hg38
56     102101          10          30
106    102569          15         495
237    103745          12          36
250    103865         119         238
273    104190          45         135
...       ...         ...         ...
20202  830010           6          12
20214  832872          50         100
20699   96609          18          36
20726   97392           4           8
20736   97893           1           2

[434 rows x 3 columns]
baitHarmonization done, and save as file: rCOGS/data/final_bait_coordinates_hg38.bed


In [32]:
## oeHarmonization (To Do: Combine Harmonization scripts)

import pandas as pd
import numpy as np

try:
    oe37 = pd.read_csv('rCOGS/data/oe_coordinates.bed', sep='\t',
                       header=0, dtype={'oeID': str}, low_memory=False)
    oe38 = pd.read_csv('rCOGS/data/oe_hg38.bed', sep='\t', header=0,
                       dtype={'oeID': str}, low_memory=False)
except FileNotFoundError as e:
    print(f"Error: File not found {e}")
except Exception as e:
    print(f"An error occurred: {e}")

# Calculate counts of each oeID in both datasets
count37_oe = oe37['oeID'].value_counts()
count38_oe = oe38['oeID'].value_counts()

# Convert to DataFrame for easier comparison
df_count37_oe = count37_oe.reset_index()
df_count37_oe.columns = ['oeID', 'count_hg19']

df_count38_oe = count38_oe.reset_index()
df_count38_oe.columns = ['oeID', 'count_hg38']

# Merge counts on oeID
merged_counts_oe = pd.merge(
    df_count37_oe, df_count38_oe, on='oeID', how='outer').fillna(0)

# Convert counts to integers after filling NA
merged_counts_oe['count_hg19'] = merged_counts_oe['count_hg19'].astype(
    int)
merged_counts_oe['count_hg38'] = merged_counts_oe['count_hg38'].astype(
    int)

# Output increased oeIDs
increased_oeIDs = merged_counts_oe[merged_counts_oe['count_hg38']
                                   > merged_counts_oe['count_hg19']]
print("Increased oeIDs in hg38 for oe datasets:")
print(increased_oeIDs[['oeID', 'count_hg19', 'count_hg38']])


# Handle increases
# oe38_merged = oe38.merge(increased_oeIDs, on='oeID', how='left')
# oe38_merged['row_number'] = oe38_merged.groupby('oeID').cumcount()
# oe38_filtered = oe38_merged[oe38_merged['row_number'] < oe38_merged['count_hg19'].fillna(float('inf'))]
# abc38 = oe38_filtered.drop(columns=['count_hg19', 'row_number','count_hg38'])
for index, row in increased_oeIDs.iterrows():
    oe_id = row['oeID']
    count_to_keep = row['count_hg19']
    rows_to_keep = oe38[oe38['oeID'] == oe_id].head(count_to_keep)
    oe38 = pd.concat([oe38[oe38['oeID'] != oe_id],
                     rows_to_keep], ignore_index=True)

print(oe38)

# Handling Missing oeID
ids_oe37 = set(oe37['oeID'])
ids_oe38 = set(oe38['oeID'])

missing_in_oe38 = ids_oe37.difference(ids_oe38)
missing_oe37_data = oe37[oe37['oeID'].isin(missing_in_oe38)]

print(missing_in_oe38)
print(missing_oe37_data)
# Create rows for missing IDs with NaN for chr, start, and end
missing_rows = [{
    'oeChr': row['oeChr'],
    'oeStart': pd.NA,
    'oeEnd': pd.NA,
    'oeID': row['oeID'],
    'baitID': row['baitID']
} for _, row in missing_oe37_data.iterrows()]

# Append missing rows to oe38 using pd.concat
missing_df = pd.DataFrame(missing_rows)
oe38 = pd.concat([oe38, missing_df], ignore_index=True)

oe38['oeStart'] = oe38['oeStart'].astype('Int64')
oe38['oeEnd'] = oe38['oeEnd'].astype('Int64')

print(oe38)

outfile = 'rCOGS/data/final_oe_coordinates_hg38.bed'
# Save the filtered hg38 dataset
oe38.to_csv(outfile, sep='\t', index=False)
print(f'oeHarmonization done and save as file: {outfile}')

Increased oeIDs in hg38 for oe datasets:
          oeID  count_hg19  count_hg38
716     102570           1           4
1406    103745           3           9
1525    103865          13          26
1742    104190          12          36
2634    106104           1           2
...        ...         ...         ...
246655   96609           1           2
247026   97392           1           2
247294   98302           1           2
247556    9872           1           2
247652   99082           2           4

[2245 rows x 3 columns]
       oeChr    oeStart      oeEnd   oeID  baitID
0          1     915239     938701    220     218
1          1     938702     940711    221     218
2          1     954044     968260    223     218
3          1     968261     992014    224     218
4          1    1271494    1277058    254     218
...      ...        ...        ...    ...     ...
728825    10  115088594  115095360  97392   97293
728826    10  118168495  118177484  98302   98134
728827     1   4

In [33]:
## Merge
from collections import Counter
import pandas as pd

# Load the data specifying low_memory=False to handle mixed types more robustly
data = pd.read_csv('rCOGS/data/PCHiC_peak_matrix_cutoff5.tsv', sep='\t',
                   dtype={'baitID': str, 'oeID': str}, low_memory=False)
bait_hg38 = pd.read_csv('rCOGS/data/final_bait_coordinates_hg38.bed', sep='\t', header=0, names=[
                        'baitChr', 'baitStart', 'baitEnd', 'baitID'], dtype={'baitID': str}, low_memory=False)
oe_hg38 = pd.read_csv('rCOGS/data/final_oe_coordinates_hg38.bed', sep='\t', header=0, names=[
                      'oeChr', 'oeStart', 'oeEnd', 'oeID', 'baitID'], dtype={'oeID': str, 'baitID': str}, low_memory=False)


# Align bait by baitID
bait_hg38['baitID'] = pd.to_numeric(bait_hg38['baitID'], errors='coerce')
data['baitID'] = pd.to_numeric(
    data['baitID'], errors='coerce', downcast='integer')

# Sort dataframes by IDs numerically
bait_hg38.sort_values(by='baitID', inplace=True)
data.sort_values(by='baitID', inplace=True)

# Reset indices of both dataframes after sorting
data.reset_index(drop=True, inplace=True)
bait_hg38.reset_index(drop=True, inplace=True)

bait_mismatch = (data['baitID'] != bait_hg38['baitID'])
if bait_mismatch.any():
    print("baitID alignment failed. Check data consistency.")
else:
    print("baitID alignment successful. Proceeding with updates.")
    data['baitChr'] = bait_hg38['baitChr'].values
    data['baitStart'] = bait_hg38['baitStart'].values
    data['baitEnd'] = bait_hg38['baitEnd'].values

print(data)
print(bait_hg38)

# Align bait by oeID
oe_hg38['oeID'] = pd.to_numeric(oe_hg38['oeID'], errors='coerce')
data['oeID'] = pd.to_numeric(
    data['oeID'], errors='coerce', downcast='integer')

oe_hg38.sort_values(by='oeID', inplace=True)
data.sort_values(by='oeID', inplace=True)

oe_hg38.reset_index(drop=True, inplace=True)
data.reset_index(drop=True, inplace=True)

print(oe_hg38)
print(data)
oe_mismatch = (data['oeID'] != oe_hg38['oeID'])
if oe_mismatch.any():
    print("oeID alignment failed. Check data consistency.")
else:
    print("oeID alignment successful. Proceeding with updates.")
    data['oeChr'] = oe_hg38['oeChr'].values
    data['oeStart'] = oe_hg38['oeStart'].values
    data['oeEnd'] = oe_hg38['oeEnd'].values

print(data)
print(oe_hg38)

# Save updated data
outfile = 'rCOGS/data/PCHiC_peak_matrix_hg38_final.tsv'
data.to_csv(outfile, sep='\t', index=False)

print(f'Bait and oe coordinates successfully updated and saved as: {outfile}')

baitID alignment successful. Proceeding with updates.
       baitChr  baitStart   baitEnd  baitID                  baitName oeChr  \
0            1     896515    912788     218  RP11-54O7.16;RP11-54O7.1     1   
1            1     896515    912788     218  RP11-54O7.16;RP11-54O7.1     1   
2            1     896515    912788     218  RP11-54O7.16;RP11-54O7.1     1   
3            1     896515    912788     218  RP11-54O7.16;RP11-54O7.1     1   
4            1     896515    912788     218  RP11-54O7.16;RP11-54O7.1     1   
...        ...        ...       ...     ...                       ...   ...   
728833       Y   20754864  20756237  835334                    RPS4Y2     Y   
728834       Y   20754864  20756237  835334                    RPS4Y2     Y   
728835       Y   20754864  20756237  835334                    RPS4Y2     Y   
728836       Y   20754864  20756237  835334                    RPS4Y2     Y   
728837       Y   21451039  21453103  835593                       NaN     Y  

In [34]:
## Annotation
import pandas as pd
import pyranges as pr
import warnings

warnings.simplefilter(action='ignore', category=FutureWarning)

# Load the PCHiC data with specific data types defined or set low_memory=False
pchic_data = pd.read_csv('rCOGS/data/PCHiC_peak_matrix_hg38_final.tsv', sep='\t', dtype={
    'baitChr': str, 'oeChr': str, 'baitID': str, 'oeID': str
}, low_memory=False)

# Rename columns to fit PyRanges requirements
pchic_data.rename(columns={
    'baitChr': 'Chromosome',
    'baitStart': 'Start',
    'baitEnd': 'End'
}, inplace=True)

# Filter out alt chromosome which is not in the main hg38
pchic_data = pchic_data[~pchic_data['Chromosome'].str.contains(
    '_alt', na=False)]

# Create PyRanges object from the entire DataFrame
pchic_ranges = pr.PyRanges(pchic_data)


# Load the annotation data and adjust column names accordingly
annotation_data = pd.read_csv('rCOGS/data/hg38_ensembl.txt', sep='\t', dtype={
                              'Chromosome/scaffold name': str, 'Strand': str})

annotation_data['Strand'] = annotation_data['Strand'].replace(
    {'1': '+', '-1': '-'})

annotation_data.rename(columns={
    'Chromosome/scaffold name': 'Chromosome',
    'Gene start (bp)': 'Start',
    'Gene end (bp)': 'End'
}, inplace=True)


# Create PyRanges object for annotation data
annotation_ranges = pr.PyRanges(annotation_data)

# Perform the join on overlapping coordinates
merged_data = pchic_ranges.join(annotation_ranges, apply_strand_suffix=False)

# Convert back to DataFrame for further manipulation or saving
merged_df = merged_data.df

# Rename and reorder columns to match your specific output requirements
merged_df.rename(columns={
    'Gene stable ID': 'ensg', 'Gene name': 'name', 'Gene type': 'biotype', 'Strand': 'strand', 'Chromosome': 'baitChr',
    'Start': 'baitStart', 'End': 'baitEnd', 'Mon': 'Monocytes', 'Mac0': 'Macrophages_M0', 'Mac1': 'Macrophages_M1',
    'Mac2': 'Macrophages_M2', 'Neu': 'Neutrophils', 'MK': 'Megakaryocytes', 'EP': 'Endothelial_precursors', 'Ery': 'Erythroblasts',
    'FoeT': 'Foetal_thymus', 'nCD4': 'Naive_CD4', 'tCD4': 'Total_CD4_MF', 'aCD4': 'Total_CD4_Activated', 'naCD4': 'Total_CD4_NonActivated',
    'nCD8': 'Naive_CD8', 'tCD8': 'Total_CD8', 'nB': 'Naive_B', 'tB': 'Total_B'
}, inplace=True)

# Example to reorder columns for final output, adjust according to your actual data structure
final_columns = [
    'ensg', 'name', 'biotype', 'strand', 'baitChr', 'baitStart', 'baitEnd',
    'baitID', 'baitName', 'oeChr', 'oeStart', 'oeEnd', 'oeID', 'oeName', 'dist',
    'Monocytes', 'Macrophages_M0', 'Macrophages_M1', 'Macrophages_M2', 'Neutrophils',
    'Megakaryocytes', 'Endothelial_precursors', 'Erythroblasts', 'Foetal_thymus',
    'Naive_CD4', 'Total_CD4_MF', 'Total_CD4_Activated', 'Total_CD4_NonActivated',
    'Naive_CD8', 'Total_CD8', 'Naive_B', 'Total_B'
]
final_df = merged_df[final_columns]

# Save to CSV if needed
outfile = 'rCOGS/data/annotated_PCHiC_peak_matrix_hg38_final.tsv'
final_df.to_csv(outfile,
                sep='\t', index=False)
print(f'Annotation successfully added and saved as: {outfile}')

Annotation successfully added and saved as: rCOGS/data/annotated_PCHiC_peak_matrix_hg38_final.tsv


In [35]:
# Process pcHiC digest file
from Bio import SeqIO
from Bio.Restriction import RestrictionBatch, Restriction
import pandas as pd

# Load restriction HindIII
rb = RestrictionBatch([Restriction.HindIII])

digest_data = {
    "chr": [],
    "start": [],
    "end": []
}

# Parse by hg38 reference genome
for genome in SeqIO.parse("rCOGS/data/hg38.fa", "fasta"):
    fragments = rb.search(genome.seq)
    for start, end in zip([1] + [x+1 for x in fragments[Restriction.HindIII]], fragments[Restriction.HindIII] + [len(genome.seq)]):
        digest_data["chr"].append(genome.id.replace(
            'chr', ''))  # Remove 'chr' prefix
        digest_data["start"].append(start)
        digest_data["end"].append(end - 1)  # Decrement end position by 1

digest_df = pd.DataFrame(digest_data)

# Filter out unwanted chromosomes
valid_chromosomes = [str(i) for i in range(1, 23)] + ['X', 'Y']
digest_df = digest_df[digest_df['chr'].isin(valid_chromosomes)]

# Assign 'fragid' after filtering
digest_df['fragid'] = range(1, len(digest_df) + 1)

# Export to a BED file

outfile = "rCOGS/data/hindIII_digest_hg38.bed"
digest_df[['chr', 'start', 'end', 'fragid']].to_csv(
    outfile, index=False, sep='\t', header=True)
print(f'pcHiC digest file successfully generated and save as: {outfile}')

pcHiC digest file successfully generated and save as: rCOGS/data/hindIII_digest_hg38.bed


In [36]:
# Process pcHiC design/annotation file
import pyranges as pr
import warnings

warnings.simplefilter(action='ignore', category=FutureWarning)

# Load your BED files into PyRanges objects
fragments = pr.read_bed("rCOGS/data/hindIII_digest_hg38.bed",as_df=False)
genes = pr.read_bed("rCOGS/data/hg38_ensembl.bed",as_df=False)


# Rename columns by accessing the underlying DataFrame
fragments_df = fragments.df
genes_df = genes.df

fragments_df.rename(columns={'Name': 'fragid'}, inplace=True)
genes_df.rename(columns={'Name': 'ensg'}, inplace=True)

# Recreate PyRanges objects with the updated DataFrames
fragments = pr.PyRanges(fragments_df)
genes = pr.PyRanges(genes_df)

chromosomes_to_keep = [str(i) for i in range(1, 23)]
chromosomes_to_keep.extend(['X', 'Y'])
filtered_fragments = fragments[fragments.Chromosome.isin(chromosomes_to_keep)]

# Use PyRanges to find overlaps using 'any' as the join type
overlaps = filtered_fragments.join(genes)

# Print or save the results
result_df = overlaps.df
selected_columns_df = result_df[['fragid', 'ensg']]
print(selected_columns_df.head())

outfile_design = 'rCOGS/data/design_PCHiC_hg38.tsv'
outfile_digest = 'rCOGS/data/filtered_hindIII_digest_hg38.tsv'

selected_columns_df.to_csv(
    outfile_design, sep='\t', index=False)

filtered_fragments_df = filtered_fragments.df
filtered_fragments_df.rename(
    columns={'Chromosome': 'chr', 'Start': 'start', 'End': 'end'}, inplace=True)

print(filtered_fragments_df)
filtered_fragments_df.to_csv(outfile_digest, sep='\t', index=False)

print(f'design annotation file successfully generated and save as: {outfile_design}')
print(f'filtered digest file successfully generated and save as: {outfile_digest}')

/Users/JerryYaw/anaconda3/envs/crossmap_env/lib/python3.9/site-packages/pyranges/readers.py:140: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(


   fragid             ensg
0       1  ENSG00000290825
1       1  ENSG00000223972
2       1  ENSG00000227232
3       2  ENSG00000227232
4       2  ENSG00000278267
       chr     start       end  fragid
0        1         1     16007       1
1        1     16009     24571       2
2        1     24573     27981       3
3        1     27983     30429       4
4        1     30431     32153       5
...     ..       ...       ...     ...
860384   Y  57205455  57205750  860385
860385   Y  57205752  57206299  860386
860386   Y  57206301  57210575  860387
860387   Y  57210577  57211010  860388
860388   Y  57211012  57227414  860389

[860389 rows x 4 columns]
design annotation file successfully generated and save as: rCOGS/data/design_PCHiC_hg38.tsv
filtered digest file successfully generated and save as: rCOGS/data/filtered_hindIII_digest_hg38.tsv


In [ ]:
# Process cSNPs file (Recommend to use HPC)
!sbash process_cSNPs.sh

In [37]:
pip install rpy2

  Using cached rpy2-3.5.16-cp39-cp39-macosx_11_0_x86_64.whl.metadata (4.5 kB)
  Using cached tzlocal-5.2-py3-none-any.whl.metadata (7.8 kB)
Using cached rpy2-3.5.16-cp39-cp39-macosx_11_0_x86_64.whl (260 kB)
Using cached tzlocal-5.2-py3-none-any.whl (17 kB)
Note: you may need to restart the kernel to use updated packages.


In [2]:
%load_ext rpy2.ipython

In [10]:
%%R
if (!requireNamespace("devtools", quietly = TRUE)) {
    install.packages("devtools", repos = "http://cran.us.r-project.org")
}
library(devtools)
install_github("ollyburren/rCOGS")
BiocManager::install("GenomicRanges")

── R CMD build ─────────────────────────────────────────────────────────────────
* checking for file ‘/private/var/folders/r3/y8lgdlvx4cx1mc2hhgvz41jh0000gn/T/RtmpMyWqpZ/remotes498a7525fd89/ollyburren-rCOGS-406074a/DESCRIPTION’ ... OK
* preparing ‘rCOGS’:
* checking DESCRIPTION meta-information ... OK
* checking for LF line-endings in source and make files and shell scripts
* checking for empty or unneeded directories
* building ‘rCOGS_0.0.0.9000.tar.gz’



* installing *source* package ‘rCOGS’ ...
** using staged installation
** R
** data
*** moving datasets to lazyload DB
** byte-compile and prepare package for lazy loading
** help
*** installing help indices
** building package indices
** installing vignettes
** testing if installed package can be loaded from temporary location
** testing if installed package can be loaded from final location
** testing if installed package keeps a record of temporary installation path
* DONE (rCOGS)


Update all/some/none? [a/s/n]: 

 all


Update all/some/none? [a/s/n]: 

...

 all


Update all/some/none? [a/s/n]: 

 a



 ダウンロードされたパッケージは、以下にあります 
 	/var/folders/r3/y8lgdlvx4cx1mc2hhgvz41jh0000gn/T//RtmpMyWqpZ/downloaded_packages 


Skipping 1 packages not available: GenomicRanges
Bioconductor version 3.18 (BiocManager 1.30.23), R 4.3.3 (2024-02-29)
Old packages: 'KernSmooth', 'broom', 'cachem', 'estimability', 'farver',
  'fastmap', 'knitr', 'openssl', 'ragg', 'rmarkdown', 'systemfonts', 'tseries',
  'xfun'
 URL 'https://cloud.r-project.org/bin/macosx/big-sur-x86_64/contrib/4.3/KernSmooth_2.23-24.tgz' を試しています 
Content type 'application/x-gzip' length 103998 bytes (101 KB)
downloaded 101 KB

 URL 'https://cloud.r-project.org/bin/macosx/big-sur-x86_64/contrib/4.3/broom_1.0.6.tgz' を試しています 
Content type 'application/x-gzip' length 1870307 bytes (1.8 MB)
downloaded 1.8 MB

 URL 'https://cloud.r-project.org/bin/macosx/big-sur-x86_64/contrib/4.3/cachem_1.1.0.tgz' を試しています 
Content type 'application/x-gzip' length 69453 bytes (67 KB)
downloaded 67 KB

 URL 'https://cloud.r-project.org/bin/macosx/big-sur-x86_64/contrib/4.3/estimability_1.5.1.tgz' を試しています 
Content type 'application/x-gzip' length 49137 bytes (47 KB)
downloa

In [4]:
%%R
library(xfun) 
library(GenomicRanges)
library(devtools)
library(rCOGS)
library(magrittr)
library(knitr)

# Loaing Recombination Data
ld.gr <- load_ld_regions('rCOGS/data/hapmap38_recomb.bed')
(ld.gr)

maf.DT <- load_ref_maf('rCOGS/data/referenced_maf.tsv',min.maf=0.05)
head(maf.DT)

t1d.DT <- load_gwas('rCOGS/data/trait_association.tsv',maf.DT,ld.gr,n.cases=5202,n.controls=1399360)
head(t1d.DT)


feature.sets <- make_pchic('rCOGS/data/annotated_PCHiC_peak_matrix_hg38_final.tsv',biotype.filter='protein_coding')
names(feature.sets)


# get a list of all genes included
all.genes <- lapply(feature.sets,function(g) unique(g$ensg)) %>% do.call('c',.) %>% unique
feature.sets[['VProm']] <- make_vprom('rCOGS/data/filtered_hindIII_digest_hg38.tsv','rCOGS/data/design_PCHiC_hg38.tsv',all.genes)

csnps.gr <- make_csnps('rCOGS/data/cSNPs_file.tsv')
head(csnps.gr)

digest.gr <- load_digest('rCOGS/data/filtered_hindIII_digest_hg38.tsv')
head(digest.gr)


# compute overall cogs score
suppressWarnings({
overall.scores <- compute_cogs(t1d.DT,csnps.gr,digest.gr,feature.sets)
})
head(overall.scores[order(cogs,decreasing = TRUE),]) %>% kable

# compute a T-cell specific score
# target_tissue<-c('Total_CD4_Activated','Total_CD4_NonActivated','Naive_CD4','Total_CD4_MF','Naive_CD8','Total_CD8')
# suppressWarnings({
# tcell.scores <- compute_cogs(t1d.DT,csnps.gr,digest.gr,feature.sets,target_tissue) %>% head()
# })
# head(tcell.scores[order(cogs,decreasing = TRUE),]) %>% kable

# sort result by cogs score
overall.scores$cogs <- as.numeric(as.character(overall.scores$cogs))
sorted_scores <- overall.scores[order(-overall.scores$cogs), ]

if (!dir.exists("results/cogs")) dir.create("results/cogs", recursive = TRUE)

outfile <- "results/cogs/cogs_results.tsv"
write.table(sorted_scores, outfile, sep="\t", quote=FALSE, row.names=FALSE)
message("File successfully saved as : ", outfile)

Adding unique identifier and filtering on MAF > 0.050000
Adding unique identifier
COGSR:load_gwas added MAF before 32010 variants after 17645
Filtering by biotypes protein_coding
Removing 5969 trans contacts
Processing 17 cell types
Processing Monocytes
Processing Macrophages_M0
Processing Macrophages_M1
Processing Macrophages_M2
Processing Neutrophils
Processing Megakaryocytes
Processing Endothelial_precursors
Processing Erythroblasts
Processing Foetal_thymus
Processing Naive_CD4
Processing Total_CD4_MF
Processing Total_CD4_Activated
Processing Total_CD4_NonActivated
Processing Naive_CD8
Processing Total_CD8
Processing Naive_B
Processing Total_B
|--------------------------------------------------|
|==================================================|
rCOGS:compute_cogs feature.names argument missing computing overall score using Monocytes,
Macrophages_M0,
Macrophages_M1,
Macrophages_M2,
Neutrophils,
Megakaryocytes,
Endothelial_precursors,
Erythroblasts,
Foetal_thymus,
Naive_CD4,
Total_

In [1]:
# Remove COGS (If you don't need anymore)
!rm -rf rCOGS

# PPI

In [ ]:
# Install Software

In [ ]:
# Query Data

In [ ]:
# Code